# PHYS 3317 -- Finite Differences in 2D

Please hand in this completed notebook before next recitation by uploading it to Blackboard

<em> Please double click on this cell, and replace its contents with your name </em>

### Utilities

In [ ]:
%pylab inline
from __future__ import division  #get rid of integer division bug

In [ ]:
from showmat import showmat #import function for printing matrices

### Formalism

We want to make a finite difference approximation to the 2D Laplacian

$$\nabla^2 \psi(x,y)= \frac{1}{\delta^2}\left[\psi(x+\delta,y)+\psi(x-\delta,y)+\psi(x,y+\delta)+\psi(x,y-\delta)-4\psi(x,y)\right]$$

The most natural representation would be as a rank 4 tensor.  That is if we define

$$\phi=\nabla^2\psi$$

Then $\phi(x,y)$ is some linear combination of $\psi(x^\prime,y^\prime)$.  Unfortunately, most software packages do not deal well with rank 4 tensors.  [For example, you can not use off-the-shelf algorithms to get their Eigenvalues.]

One approach is to number the points on our 2D grid, and think of it as a 1D list.  For example, imagine we have a $3\times 3$ grid:

In [ ]:
mesh=arange(9,dtype=integer).reshape(3,3)
mesh

These numbers will label the points so that

$$ \begin{array}{c}
\psi_0=\psi(x=0,y=0)\cr \psi_1=\psi(x=1,y=0)\cr \psi_2=\psi(x=2,y=0)\cr \psi_3=\psi(x=0,y=1)\cr
\psi_4=\psi(x=1,y=1)\cr
\psi_5=\psi(x=2,y=1)\cr
\psi_6=\psi(x=0,y=2)\cr
\psi_7=\psi(x=1,y=2)\cr
\psi_8=\psi(x=2,y=2)
\end{array}$$

We need a function which takes a vector $\psi_1,\psi_2,\cdots$ and rearanges them into the right geometric order

In [ ]:
def twodrep(vec):
    """ twodrep reshapes a linear array into a square array"""
    size=int(sqrt(len(vec))) # How many psi's do we have
    ans=vec.copy() # So as not to cause any nasty side-effects, lets copy the array
    return ans.reshape(size,size) # reshape

In [ ]:
test=array((0,0,0,0,1,0,0,0,0)) # sample array of 9 elements

In [ ]:
testarray=twodrep(test)  # wrap it into a square
testarray                # display the result

In [ ]:
showmat(testarray)  # here is a fancy display function 

### Generating The Laplacian

We now generate the laplacian -- here I will take dx=1, but we can scale it later.  First lets just make an empty matrix

In [ ]:
laplacematrix=zeros((9,9))
showmat(laplacematrix)

Now lets set the diagonal elements.  We will use some cool notation

In [ ]:
# set diagonal elements
laplacematrix[mesh,mesh]=-4
showmat(laplacematrix)

Next let us set all of the shifted one-to-the right elements.  Since we can't hop to the right from the rightmost elements (unless we use periodic boundary conditions) we need to generate a matrix which has the last column of mesh removed

In [ ]:
left=mesh[:,:-1]
left

You might want to play with this notation a bit -- its really cool. [Click here for some array tips](http://pages.physics.cornell.edu/~myers/teaching/ComputationalMethods/python/arrays.html) 

We do the same thing with the right

In [ ]:
right=mesh[:,1:]
right

setting the hopping right terms is then easy

In [ ]:
laplacematrix[[left,right]]=1
showmat(laplacematrix)

<b> Problem:</b> In our 1D example of finite difference, all of the entries one from the diagonal were set to 1.  This one has some zeros.  Why?

<em> Write answer here </em>

hopping left is just

In [ ]:
laplacematrix[[right,left]]=1
showmat(laplacematrix)

The 3x3 blocks which correspond to individual rows should be clear

<b> Problem:</b> Write code to add the hopping up and down terms to laplacematrix

<b> Problem:</b>Test your code by seeing what it does to our test vector

In [ ]:
showmat(twodrep(laplacematrix.dot(test)))

### Now with Sparse Arrays

We can be more efficient if we use sparse arrays so that we don't store all of those zeros

In [ ]:
from scipy.sparse import *  # loads the required functions

We will use the "dictionary of keys" form of a sparse matrix.  [For our 1D arrays we used the dia_matrix format for this, but I find the dok syntax more transparent for this applications.  There is a slight numerical efficiency gained by using dia_matrix, but this is more than offset by the ease of construction.]

In [ ]:
dok_matrix?

In [ ]:
sparselaplace=dok_matrix((9,9))
sparselaplace

In [ ]:
showmat(sparselaplace)

We can just use our old notation

In [ ]:
sparselaplace[mesh,mesh]=-4

In [ ]:
sparselaplace[mesh,mesh]=-4
sparselaplace[left,right]=1
sparselaplace[right,left]=1
showmat(sparselaplace)

Add the up and down hoppings -- make sure everything works

Now lets encapsulate this into a function

In [ ]:
def makelaplacematrix(numgridpoints,dx):
    """makelaplacematrix(numgridpoints,dx) returns a (numgridpoints^2)x(numgridpoints^2) square matrix
    which represents the laplacian on the 2d grid with grid spacing dx.  It is in the dok_matrix format,
    and has hard wall boundary conditions"""
    # fill in code
    return #put matrix which is returned

Test with the following code:  you should get -400 on the diagonal, and 100's in a few other places

In [ ]:
lmat=makelaplacematrix(10,0.1)
showmat(lmat

In [ ]:
test2=zeros(100)
test2[45]=1
showmat(twodrep(test2))

In [ ]:
test3=lmat.dot(test2)
showmat(twodrep(test3))

In [ ]:
test4=zeros(100)
test4[40]=1
showmat(twodrep(test4))

In [ ]:
test5=lmat.dot(test4)
showmat(twodrep(test5))

### Application: Two dimensional particle in a box eigenstates

Here I show how to apply this technique to finding the eigenstates of a 2D hard wall box

In [ ]:
from scipy.sparse.linalg import eigsh  # load the function which calculates eigenvectors of hermitian matrices

In [ ]:
boxham=csc_matrix(-0.5*makelaplacematrix(50,0.02))

In [ ]:
boxham

In [ ]:
energies,states=eigsh(boxham, k=10, sigma=0., return_eigenvectors=True)

In [ ]:
energies

We can compare this to what we expect the exact answer to be

In [ ]:
vals=array([[pi**2*(n**2+m**2)/2 for n in arange(1,5)] for m in arange(1,5)]).flatten()
vals.sort()
vals

We can also plot some of the wavefunctions

In [ ]:
imshow(abs(twodrep(states[:,0]))**2)

In [ ]:
imshow(abs(twodrep(states[:,1]))**2)

In [ ]:
imshow(abs(twodrep(states[:,2]))**2)

These last two state are degenerate

In [ ]:
print(energies[1],energies[2])

Thus linear combinations are also eigenstates:

In [ ]:
imshow(abs(twodrep(states[:,1]+states[:,2]))**2)

In [ ]:
imshow(abs(twodrep(states[:,1]-states[:,2]))**2)

For fun, here is a higher mode

In [ ]:
en,st=eigsh(boxham, k=1, sigma=520., return_eigenvectors=True)

In [ ]:
imshow(abs(twodrep(st[:,0]))**2)

## Potentials

Suppose we have a 2D potential on our grid.  For example, here is a 2D harmonic oscillator potential on a grid running from -2 to 2 in steps of 0.5

In [ ]:
potvals=array([[(x**2+y**2)/2 for x in arange(-2,2,0.5)] 
               for y in arange(-2,2,0.5)])

In [ ]:
imshow(potvals)

To make the potential matrix we first "unwrap" this grid into a linear list of numbers.  First we need to know how many pixels we have.

In [ ]:
numpixels=product(potvals.shape)
numpixels

We unwrap them via

In [ ]:
unwrapped=potvals.reshape(numpixels)
plot(unwrapped,"o")

Our potential matrix will be a 64x64 matrix that when applied to the 64 values of psi, multiplies each of them by $V$ at that site

In [ ]:
potmat=dia_matrix((unwrapped,0),shape=[numpixels,numpixels])

In [ ]:
showmat(potmat)

We can encapsulate this via

In [ ]:
def makepotmat(potvals):
    numpixels=product(potvals.shape)
    unwrapped=potvals.reshape(numpixels)
    return dia_matrix((unwrapped,0),shape=[numpixels,numpixels])

## Problem

Numerically find the energies of the first 5 eigenstates of a 2D Harmonic Oscillator.  Use a 40x40 grid with $x$ running from -4 to 4 in steps of 0.2, and y running from -4 to 4 in steps of 0.2.  Use units where the mass, $\hbar$ and $\omega$ are all 1.  